# Processing data

In [55]:
import pandas as pd

In [56]:
wiki_data = pd.read_csv('data/wikipedia/subsetted_wiki_data_full_text.csv')

In [57]:
import os
import random
import codecs
from collections import defaultdict

from gensim.models.ldamodel import LdaModel as Lda
from gensim import corpora
from nltk.corpus import stopwords 
from nltk.stem.porter import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer
from nltk import word_tokenize
from nltk import pos_tag

import enchant
spelling_dict = enchant.Dict("en_US")

stop = set(stopwords.words('english'))
lemma = WordNetLemmatizer()
stemmer = PorterStemmer()

stemmed_dict = defaultdict(set)

def stem_and_update_stem_dict(tokens):
    output_list = []
    for token in tokens:
        stemmed = stemmer.stem(token)
        if stemmed != token:
            stemmed_dict[stemmed].add(token)
        output_list.append(stemmed)
    return output_list
        
list_of_POS_to_ignore = ['WRB', 'WP$', 'WP',  'WDT', 'UH', 
                         'TO', 'RP', 'RBS', 'RBR', 'PRP$', 'PRP', 
                        'MD', 'JJS', 'JJR', 'JJ', 'IN', 'FW', 'EX', 
                         'DT', 'CD']

# Function to remove stop words from sentences & lemmatize verbs. 
def clean(doc):
    tokens = word_tokenize(doc)
    #removing stop words 
    tokens = [i for i in tokens if i not in stop]
    # removing pos data 
    tokens = [word for word, pos in pos_tag(tokens) if pos not in list_of_POS_to_ignore]
    # Removing improperly spelled words (pronouns must be capitalized to be spelled right)
    tokens = [word for word in tokens if spelling_dict.check(word)]
    # lowercase
    tokens = [word.lower() for word in tokens]
    # lemmatized
    tokens = [lemma.lemmatize(word, 'v') for word in tokens]
    # removing short words 
    tokens = [s for s in tokens if len(s) > 2]
    # stemmed
    tokens = stem_and_update_stem_dict(tokens)
    
    return tokens

In [58]:
tokenized_text = wiki_data.text.apply(lambda x: clean(str(x)))

In [118]:
from gensim import corpora

dictionary = corpora.Dictionary(tokenized_text)

In [119]:
original_words = set(dictionary.token2id.keys())

In [120]:
len(original_words)

30139

In [121]:
dictionary.filter_extremes(no_below=3, no_above=0.4)

In [122]:
reduced_number = set(dictionary.token2id.keys())
len(reduced_number)

23814

In [123]:
# Remove the 50 most common words that showed up
dictionary.filter_n_most_frequent(50)

In [124]:
reduced_number - set(dictionary.token2id.keys())

{'age',
 'also',
 'american',
 'area',
 'bear',
 'becom',
 'begin',
 'call',
 'citi',
 'come',
 'countri',
 'die',
 'find',
 'first',
 'get',
 'give',
 'group',
 'histori',
 'includ',
 'know',
 'later',
 'list',
 'live',
 'make',
 'mean',
 'member',
 'name',
 'nation',
 'new',
 'page',
 'part',
 'peopl',
 'place',
 'play',
 'relat',
 'say',
 'show',
 'start',
 'state',
 'take',
 'time',
 'unit',
 'univers',
 'use',
 'websit',
 'well',
 'work',
 'world',
 'write',
 'year'}

In [125]:
# Define the corpus with the narrowed dictionary
corpus = [dictionary.doc2bow(text) for text in tokenized_text]

In [126]:
import os
import gensim

In [127]:
import gensim

for number_of_topics in [100, 200, 500, 1000]:
    NUM_TOPICS = number_of_topics
    ldamodel = gensim.models.ldamodel.LdaModel(corpus, id2word=dictionary, num_topics = NUM_TOPICS, 
                                               chunksize=1000, iterations=100, passes=30)
    
    title = '180922_wikipedia_model.stemmed.' + str(number_of_topics) + '.gensim.'

    ldamodel.save(os.path.join('models', title))

    topics = ldamodel.print_topics(num_words=4, num_topics=number_of_topics)

    for topic in topics:
        print(topic)

/home/wmvoje/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1023: RuntimeWarning: divide by zero encountered in log
  diff = np.log(self.expElogbeta)


(0, '0.104*"centuri" + 0.065*"empir" + 0.051*"roman" + 0.036*"greek"')
(1, '0.164*"germani" + 0.075*"german" + 0.069*"victoria" + 0.051*"flag"')
(2, '0.173*"color" + 0.087*"fli" + 0.072*"prize" + 0.052*"wing"')
(3, '0.079*"system" + 0.053*"comput" + 0.034*"inform" + 0.029*"program"')
(4, '0.134*"food" + 0.062*"eat" + 0.062*"spring" + 0.054*"farm"')
(5, '0.046*"sport" + 0.045*"olymp" + 0.042*"game" + 0.041*"cup"')
(6, '0.147*"engin" + 0.144*"design" + 0.027*"composit" + 0.026*"cathedr"')
(7, '0.209*"south" + 0.108*"australia" + 0.084*"america" + 0.071*"north"')
(8, '0.348*"counti" + 0.053*"locat" + 0.046*"massachusett" + 0.038*"town"')
(9, '0.160*"build" + 0.066*"hous" + 0.042*"bridg" + 0.028*"cross"')
(10, '0.150*"king" + 0.108*"church" + 0.060*"christian" + 0.056*"cathol"')
(11, '0.100*"earth" + 0.099*"star" + 0.048*"sun" + 0.043*"planet"')
(12, '0.108*"anim" + 0.091*"love" + 0.057*"fall" + 0.055*"friend"')
(13, '0.090*"court" + 0.036*"jackson" + 0.031*"white" + 0.030*"crime"')
(14, '

KeyboardInterrupt: 

In [130]:
# Set up log to terminal
import logging
logging.basicConfig(filename='lda_model.log', 
                    format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)


In [132]:
import gensim

for number_of_topics in [500, 1000]:
    NUM_TOPICS = number_of_topics
    ldamodel = gensim.models.ldamodel.LdaModel(corpus, id2word=dictionary, num_topics = NUM_TOPICS, 
                                               chunksize=1000, iterations=100, passes=30)
    
    title = '180922_wikipedia_model.stemmed.' + str(number_of_topics) + '.gensim.'

    ldamodel.save(os.path.join('models', title))

    topics = ldamodel.print_topics(num_words=4, num_topics=number_of_topics)

    for topic in topics:
        print(topic)

2018-09-23 11:22:41,401 : INFO : using symmetric alpha at 0.002
2018-09-23 11:22:41,405 : INFO : using symmetric eta at 0.002
2018-09-23 11:22:41,420 : INFO : using serial LDA version on this node
2018-09-23 11:22:45,304 : INFO : running online (multi-pass) LDA training, 500 topics, 30 passes over the supplied corpus of 70000 documents, updating model once every 1000 documents, evaluating perplexity every 10000 documents, iterating 100x with a convergence threshold of 0.001000
2018-09-23 11:22:45,305 : INFO : PROGRESS: pass 0, at document #1000/70000
2018-09-23 11:22:56,104 : INFO : merging changes from 1000 documents into a model of 70000 documents
2018-09-23 11:23:02,256 : INFO : topic #356 (0.002): 0.055*"valley" + 0.026*"music" + 0.023*"kingdom" + 0.023*"ireland" + 0.023*"assembl" + 0.023*"northern" + 0.023*"brown" + 0.023*"award" + 0.020*"album" + 0.016*"chri"
2018-09-23 11:23:02,258 : INFO : topic #379 (0.002): 0.073*"data" + 0.073*"provinc" + 0.037*"structur" + 0.037*"protein" +

2018-09-23 11:24:03,397 : INFO : topic #399 (0.002): 0.172*"california" + 0.127*"accid" + 0.120*"navi" + 0.079*"resid" + 0.057*"francisco" + 0.031*"effort" + 0.028*"juli" + 0.027*"air" + 0.026*"mason" + 0.026*"zealand"
2018-09-23 11:24:03,451 : INFO : topic diff=inf, rho=0.408248
2018-09-23 11:24:03,470 : INFO : PROGRESS: pass 0, at document #7000/70000
2018-09-23 11:24:08,821 : INFO : merging changes from 1000 documents into a model of 70000 documents
2018-09-23 11:24:14,978 : INFO : topic #328 (0.002): 0.336*"languag" + 0.097*"english" + 0.059*"speak" + 0.051*"dutch" + 0.035*"latin" + 0.034*"angl" + 0.031*"word" + 0.025*"old" + 0.016*"anglo" + 0.015*"norman"
2018-09-23 11:24:14,982 : INFO : topic #499 (0.002): 0.115*"softwar" + 0.059*"machin" + 0.052*"everi" + 0.050*"comput" + 0.047*"system" + 0.044*"process" + 0.032*"axi" + 0.030*"oper" + 0.024*"appli" + 0.021*"audi"
2018-09-23 11:24:14,984 : INFO : topic #341 (0.002): 0.279*"king" + 0.154*"son" + 0.093*"brother" + 0.084*"titl" + 0.

2018-09-23 11:25:21,948 : INFO : topic diff=inf, rho=0.288675
2018-09-23 11:25:21,961 : INFO : PROGRESS: pass 0, at document #13000/70000
2018-09-23 11:25:27,171 : INFO : merging changes from 1000 documents into a model of 70000 documents
2018-09-23 11:25:33,385 : INFO : topic #275 (0.002): 0.582*"war" + 0.095*"command" + 0.069*"civil" + 0.059*"armi" + 0.056*"fight" + 0.030*"militari" + 0.026*"union" + 0.023*"secretari" + 0.017*"march" + 0.008*"retir"
2018-09-23 11:25:33,391 : INFO : topic #80 (0.002): 0.727*"type" + 0.159*"brain" + 0.081*"tumor" + 0.026*"dementia" + 0.001*"treatment" + 0.000*"cell" + 0.000*"thalidomid" + 0.000*"surgic" + 0.000*"radiotherapi" + 0.000*"outward"
2018-09-23 11:25:33,397 : INFO : topic #466 (0.002): 0.328*"lose" + 0.159*"probabl" + 0.153*"ever" + 0.142*"tag" + 0.080*"albert" + 0.030*"liverpool" + 0.030*"appear" + 0.028*"automat" + 0.022*"dock" + 0.014*"tooth"
2018-09-23 11:25:33,407 : INFO : topic #314 (0.002): 0.391*"found" + 0.164*"confer" + 0.115*"athle

2018-09-23 11:26:41,309 : INFO : topic #146 (0.002): 0.374*"retriev" + 0.190*"com" + 0.083*"committe" + 0.083*"recogn" + 0.057*"dollar" + 0.033*"athlet" + 0.030*"horror" + 0.027*"abbrevi" + 0.026*"sportsperson" + 0.023*"thriller"
2018-09-23 11:26:41,316 : INFO : topic #201 (0.002): 0.235*"protect" + 0.123*"babi" + 0.061*"mammal" + 0.055*"skeleton" + 0.047*"endang" + 0.034*"ear" + 0.032*"speci" + 0.027*"vibrat" + 0.025*"reef" + 0.025*"birth"
2018-09-23 11:26:41,319 : INFO : topic #292 (0.002): 0.147*"win" + 0.111*"player" + 0.084*"point" + 0.054*"game" + 0.033*"score" + 0.031*"end" + 0.028*"beat" + 0.027*"run" + 0.026*"back" + 0.023*"kick"
2018-09-23 11:26:41,322 : INFO : topic #459 (0.002): 0.141*"sex" + 0.082*"partner" + 0.076*"growth" + 0.071*"pollut" + 0.060*"size" + 0.056*"height" + 0.033*"stretch" + 0.032*"friction" + 0.023*"environment" + 0.021*"condom"
2018-09-23 11:26:41,326 : INFO : topic #259 (0.002): 0.285*"lord" + 0.070*"effici" + 0.053*"lieuten" + 0.045*"threat" + 0.044*"o

2018-09-23 11:27:57,986 : INFO : topic #94 (0.002): 0.340*"camp" + 0.305*"rank" + 0.129*"malaysia" + 0.044*"norwegian" + 0.039*"abdul" + 0.032*"least" + 0.030*"higher" + 0.019*"med" + 0.014*"graveyard" + 0.011*"norway"
2018-09-23 11:27:57,988 : INFO : topic #85 (0.002): 0.358*"children" + 0.158*"parent" + 0.143*"loui" + 0.067*"hundr" + 0.057*"restor" + 0.038*"napoleon" + 0.019*"candi" + 0.018*"xvi" + 0.015*"famili" + 0.014*"bonapart"
2018-09-23 11:27:57,991 : INFO : topic #390 (0.002): 0.221*"board" + 0.207*"trade" + 0.117*"peac" + 0.112*"israel" + 0.073*"former" + 0.069*"agreement" + 0.056*"free" + 0.043*"director" + 0.019*"end" + 0.012*"establish"
2018-09-23 11:27:57,998 : INFO : topic #483 (0.002): 0.158*"decis" + 0.146*"citat" + 0.116*"agre" + 0.091*"louisiana" + 0.076*"famou" + 0.053*"orlean" + 0.053*"wisdom" + 0.047*"otto" + 0.041*"chipmunk" + 0.039*"decid"
2018-09-23 11:27:58,047 : INFO : topic diff=inf, rho=0.200000
2018-09-23 11:27:58,057 : INFO : PROGRESS: pass 0, at document

...

2018-09-24 13:00:08,839 : INFO : topic #756 (0.001): 0.112*"louis" + 0.091*"clan" + 0.079*"philipp" + 0.074*"duchess"
2018-09-24 13:00:08,841 : INFO : topic #757 (0.001): 0.188*"theori" + 0.119*"physic" + 0.114*"particl" + 0.096*"explain"
2018-09-24 13:00:08,844 : INFO : topic #758 (0.001): 0.793*"rock" + 0.052*"goat" + 0.039*"permit" + 0.032*"shelter"
2018-09-24 13:00:08,848 : INFO : topic #759 (0.001): 0.618*"scotland" + 0.115*"pollut" + 0.073*"glen" + 0.069*"older"
2018-09-24 13:00:08,850 : INFO : topic #760 (0.001): 0.457*"model" + 0.320*"electron" + 0.095*"rocket" + 0.069*"assign"
2018-09-24 13:00:08,852 : INFO : topic #761 (0.001): 0.491*"ball" + 0.410*"leg" + 0.077*"photographi" + 0.012*"delic"
2018-09-24 13:00:08,854 : INFO : topic #762 (0.001): 0.302*"skill" + 0.205*"rid" + 0.125*"dave" + 0.088*"harper"
2018-09-24 13:00:08,856 : INFO : topic #763 (0.001): 0.000*"intimaci" + 0.000*"curious" + 0.000*"snippet" + 0.000*"onstag"
2018-09-24 13:00:08,859 : INFO : topic #764 (0.001): 

2018-09-24 13:00:09,033 : INFO : topic #825 (0.001): 0.468*"asia" + 0.204*"arkansa" + 0.141*"slightli" + 0.095*"nepal"
2018-09-24 13:00:09,035 : INFO : topic #826 (0.001): 0.412*"liquid" + 0.194*"genet" + 0.124*"honey" + 0.104*"ant"
2018-09-24 13:00:09,038 : INFO : topic #827 (0.001): 0.497*"tri" + 0.247*"much" + 0.076*"howev" + 0.053*"kick"
2018-09-24 13:00:09,041 : INFO : topic #828 (0.001): 0.290*"egg" + 0.196*"thousand" + 0.161*"lay" + 0.050*"hatch"
2018-09-24 13:00:09,044 : INFO : topic #829 (0.001): 0.354*"activ" + 0.225*"femal" + 0.210*"hunt" + 0.054*"genera"
2018-09-24 13:00:09,054 : INFO : topic #830 (0.001): 0.772*"see" + 0.088*"spot" + 0.042*"disappear" + 0.040*"hemispher"
2018-09-24 13:00:09,057 : INFO : topic #831 (0.001): 0.480*"chapter" + 0.354*"miami" + 0.148*"imprison" + 0.000*"outward"
2018-09-24 13:00:09,059 : INFO : topic #832 (0.001): 0.381*"pet" + 0.277*"syndrom" + 0.167*"strain" + 0.050*"autism"
2018-09-24 13:00:09,070 : INFO : topic #833 (0.001): 0.166*"golf" + 

2018-09-24 13:00:09,223 : INFO : topic #895 (0.001): 0.900*"machin" + 0.079*"virtual" + 0.012*"emul" + 0.000*"intimaci"
2018-09-24 13:00:09,226 : INFO : topic #896 (0.001): 0.334*"squar" + 0.280*"wisconsin" + 0.170*"creek" + 0.102*"allen"
2018-09-24 13:00:09,228 : INFO : topic #897 (0.001): 0.406*"carlo" + 0.330*"pepper" + 0.103*"carolin" + 0.060*"chili"
2018-09-24 13:00:09,230 : INFO : topic #898 (0.001): 0.000*"intimaci" + 0.000*"curious" + 0.000*"snippet" + 0.000*"onstag"
2018-09-24 13:00:09,232 : INFO : topic #899 (0.001): 0.376*"environ" + 0.192*"inspir" + 0.063*"avatar" + 0.060*"attitud"
2018-09-24 13:00:09,235 : INFO : topic #900 (0.001): 0.000*"intimaci" + 0.000*"curious" + 0.000*"snippet" + 0.000*"onstag"
2018-09-24 13:00:09,237 : INFO : topic #901 (0.001): 0.000*"intimaci" + 0.000*"curious" + 0.000*"snippet" + 0.000*"onstag"
2018-09-24 13:00:09,240 : INFO : topic #902 (0.001): 0.758*"saint" + 0.056*"loir" + 0.055*"just" + 0.021*"belong"
2018-09-24 13:00:09,242 : INFO : topic 

2018-09-24 13:00:09,392 : INFO : topic #965 (0.001): 0.295*"medic" + 0.292*"ill" + 0.229*"marshal" + 0.159*"stress"
2018-09-24 13:00:09,394 : INFO : topic #966 (0.001): 0.397*"broadcast" + 0.321*"hospit" + 0.131*"emmi" + 0.089*"creator"
2018-09-24 13:00:09,397 : INFO : topic #967 (0.001): 0.676*"wood" + 0.114*"susan" + 0.078*"prairi" + 0.049*"younger"
2018-09-24 13:00:09,399 : INFO : topic #968 (0.001): 0.191*"wed" + 0.173*"kiss" + 0.090*"that" + 0.077*"randi"
2018-09-24 13:00:09,401 : INFO : topic #969 (0.001): 0.276*"architectur" + 0.192*"cathedr" + 0.161*"chapel" + 0.061*"basilica"
2018-09-24 13:00:09,406 : INFO : topic #970 (0.001): 0.406*"pennsylvania" + 0.171*"immigr" + 0.143*"pittsburgh" + 0.077*"yale"
2018-09-24 13:00:09,413 : INFO : topic #971 (0.001): 0.830*"divis" + 0.144*"fort" + 0.012*"dhaka" + 0.009*"chittagong"
2018-09-24 13:00:09,419 : INFO : topic #972 (0.001): 0.451*"ten" + 0.346*"chri" + 0.069*"def" + 0.058*"boyfriend"
2018-09-24 13:00:09,423 : INFO : topic #973 (0.0

(0, '0.449*"second" + 0.394*"champion" + 0.140*"tournament" + 0.007*"kasparov"')
(1, '0.323*"revolut" + 0.263*"and" + 0.196*"futur" + 0.115*"liberti"')
(2, '0.237*"safeti" + 0.218*"hawaii" + 0.166*"moment" + 0.116*"asian"')
(3, '0.765*"japan" + 0.111*"vietnam" + 0.103*"japanes" + 0.018*"vietnames"')
(4, '0.293*"dead" + 0.271*"miller" + 0.144*"marilyn" + 0.087*"montgomeri"')
(5, '0.291*"altern" + 0.232*"output" + 0.228*"instruct" + 0.138*"slow"')
(6, '0.445*"object" + 0.119*"disk" + 0.098*"belt" + 0.080*"dwarf"')
(7, '0.998*"team" + 0.000*"snippet" + 0.000*"intimaci" + 0.000*"curious"')
(8, '0.901*"park" + 0.096*"stream" + 0.000*"snippet" + 0.000*"invoc"')
(9, '0.471*"alabama" + 0.320*"occupi" + 0.198*"birmingham" + 0.000*"curious"')
(10, '0.451*"earth" + 0.186*"sun" + 0.164*"planet" + 0.090*"decad"')
(11, '0.349*"saw" + 0.141*"wit" + 0.073*"coup" + 0.056*"regim"')
(12, '0.996*"power" + 0.000*"onstag" + 0.000*"intimaci" + 0.000*"curious"')
(13, '0.292*"psycholog" + 0.255*"behavior" + 0.

In [141]:
ldamodel.print_topics(num_words=4, num_topics=100)

2018-09-24 13:22:30,702 : INFO : topic #570 (0.001): 0.473*"project" + 0.150*"content" + 0.107*"basic" + 0.092*"lock"
2018-09-24 13:22:30,705 : INFO : topic #127 (0.001): 0.431*"tell" + 0.298*"break" + 0.068*"floor" + 0.056*"instead"
2018-09-24 13:22:30,708 : INFO : topic #82 (0.001): 0.268*"cut" + 0.195*"appli" + 0.189*"edg" + 0.163*"actual"
2018-09-24 13:22:30,711 : INFO : topic #79 (0.001): 0.157*"gordon" + 0.110*"duck" + 0.105*"graham" + 0.105*"jeff"
2018-09-24 13:22:30,713 : INFO : topic #838 (0.001): 0.305*"ben" + 0.292*"facil" + 0.142*"laura" + 0.100*"algeria"
2018-09-24 13:22:30,716 : INFO : topic #154 (0.001): 0.962*"game" + 0.027*"assum" + 0.009*"elit" + 0.000*"intimaci"
2018-09-24 13:22:30,719 : INFO : topic #411 (0.001): 0.266*"fraser" + 0.226*"hank" + 0.173*"parliamentari" + 0.167*"groom"
2018-09-24 13:22:30,722 : INFO : topic #61 (0.001): 0.217*"pin" + 0.168*"dri" + 0.104*"reproduct" + 0.092*"plat"
2018-09-24 13:22:30,725 : INFO : topic #533 (0.001): 0.697*"affair" + 0.13

2018-09-24 13:22:30,958 : INFO : topic #994 (0.001): 0.469*"mari" + 0.234*"parliament" + 0.188*"ann" + 0.085*"debat"
2018-09-24 13:22:30,962 : INFO : topic #67 (0.001): 0.209*"franz" + 0.161*"ground" + 0.150*"ace" + 0.137*"heath"
2018-09-24 13:22:30,964 : INFO : topic #686 (0.001): 0.795*"region" + 0.054*"saudi" + 0.051*"export" + 0.048*"basket"
2018-09-24 13:22:30,968 : INFO : topic #851 (0.001): 0.315*"messag" + 0.269*"question" + 0.123*"answer" + 0.096*"listen"
2018-09-24 13:22:30,975 : INFO : topic #925 (0.001): 0.471*"retriev" + 0.454*"novemb" + 0.042*"rabbit" + 0.011*"theresa"
2018-09-24 13:22:30,978 : INFO : topic #748 (0.001): 0.672*"sport" + 0.099*"nbc" + 0.060*"info" + 0.058*"nascar"
2018-09-24 13:22:30,981 : INFO : topic #84 (0.001): 0.996*"popul" + 0.000*"intimaci" + 0.000*"dario" + 0.000*"outward"
2018-09-24 13:22:30,984 : INFO : topic #479 (0.001): 0.436*"final" + 0.328*"entertain" + 0.107*"fantasi" + 0.051*"recept"
2018-09-24 13:22:30,986 : INFO : topic #116 (0.001): 0.3

[(570, '0.473*"project" + 0.150*"content" + 0.107*"basic" + 0.092*"lock"'),
 (127, '0.431*"tell" + 0.298*"break" + 0.068*"floor" + 0.056*"instead"'),
 (82, '0.268*"cut" + 0.195*"appli" + 0.189*"edg" + 0.163*"actual"'),
 (79, '0.157*"gordon" + 0.110*"duck" + 0.105*"graham" + 0.105*"jeff"'),
 (838, '0.305*"ben" + 0.292*"facil" + 0.142*"laura" + 0.100*"algeria"'),
 (154, '0.962*"game" + 0.027*"assum" + 0.009*"elit" + 0.000*"intimaci"'),
 (411,
  '0.266*"fraser" + 0.226*"hank" + 0.173*"parliamentari" + 0.167*"groom"'),
 (61, '0.217*"pin" + 0.168*"dri" + 0.104*"reproduct" + 0.092*"plat"'),
 (533, '0.697*"affair" + 0.137*"forb" + 0.059*"dewey" + 0.038*"supervisor"'),
 (810, '0.445*"milk" + 0.237*"dorothi" + 0.221*"dive" + 0.039*"mauritiu"'),
 (163, '0.274*"forest" + 0.113*"habitat" + 0.068*"nest" + 0.057*"dinner"'),
 (539, '0.365*"great" + 0.353*"bird" + 0.194*"littl" + 0.071*"matthew"'),
 (777, '0.385*"boe" + 0.293*"punjab" + 0.111*"variant" + 0.081*"frontier"'),
 (216, '0.426*"decid" + 0.3

# Loading in a model

In [138]:
sample_model = Lda.load('models/180918_wikipedia_model.500.gensim.')

2018-09-24 13:10:12,213 : INFO : loading LdaModel object from models/180918_wikipedia_model.500.gensim.
2018-09-24 13:10:12,218 : INFO : loading expElogbeta from models/180918_wikipedia_model.500.gensim..expElogbeta.npy with mmap=None
2018-09-24 13:10:12,272 : INFO : setting ignored attribute state to None
2018-09-24 13:10:12,274 : INFO : setting ignored attribute dispatcher to None
2018-09-24 13:10:12,276 : INFO : setting ignored attribute id2word to None
2018-09-24 13:10:12,278 : INFO : loaded models/180918_wikipedia_model.500.gensim.
2018-09-24 13:10:12,279 : INFO : loading LdaState object from models/180918_wikipedia_model.500.gensim..state
2018-09-24 13:10:12,282 : INFO : loading sstats from models/180918_wikipedia_model.500.gensim..state.sstats.npy with mmap=None
2018-09-24 13:10:12,336 : INFO : loaded models/180918_wikipedia_model.500.gensim..state


In [140]:
sample_model.()

TypeError: log_perplexity() missing 1 required positional argument: 'chunk'

In [8]:
topics = sample_model.print_topics(num_words=10, num_topics=50)

for topic in topics:
    print(topic)

(411, '0.156*"detroit" + 0.108*"eagle" + 0.095*"kelly" + 0.089*"duck" + 0.064*"tigers" + 0.061*"flame" + 0.055*"lions" + 0.042*"calgary" + 0.033*"anaheim" + 0.027*"panthers"')
(237, '0.215*"animals" + 0.183*"animal" + 0.080*"hunt" + 0.051*"mammal" + 0.043*"prey" + 0.036*"eat" + 0.033*"insect" + 0.032*"humans" + 0.028*"large" + 0.017*"estuary"')
(355, '0.491*"john" + 0.132*"peter" + 0.041*"matthew" + 0.034*"studios" + 0.024*"jennifer" + 0.013*"dover" + 0.013*"groove" + 0.013*"last" + 0.012*"lopez" + 0.012*"classics"')
(398, '0.422*"france" + 0.123*"commune" + 0.084*"departments" + 0.060*"department" + 0.058*"region" + 0.054*"regions" + 0.031*"alpes" + 0.019*"rhône" + 0.019*"kid" + 0.018*"côte"')
(441, '0.133*"clear" + 0.115*"rid" + 0.083*"margaret" + 0.067*"suit" + 0.058*"pig" + 0.051*"childhood" + 0.041*"aspects" + 0.034*"discussion" + 0.027*"habit" + 0.026*"welcome"')
(73, '0.220*"information" + 0.194*"data" + 0.147*"send" + 0.078*"climate" + 0.055*"punjab" + 0.047*"settle" + 0.031*"h